## Fantasy Premier League Classic Mini League Bar Chart Race
### Date Modified: 25th May, 2021

This notebook can be used for creating a bar chart race for a FPL classic mini league. The code pulls manager performace data from the FPL API, transforms it and creates a bar chart race. User needs to input the classic league id and the number of managers for which the chart has to be created.

In [1]:
# Importing required packages
import pandas as pd
pd. set_option('display.max_columns', 100)
import requests
import bar_chart_race as bcr

### Defining Functions to Pull and Transform Data from FPL API

In [2]:
def classic_league_gw_data(league_id):
    '''
    Function to pull  manager details and GW level performance of each manager in the classic league.
    In case a league has more than 50 managers, it pulls the top 50 managers by rank. 
    
        Parameters:
            league_id: Id of the classic league, can be obtained from the URL of the classic league
            
        Returns:
            manager_gw_perf_df: Dataframe containing manager details and GW performance metrics such as GW points, 
            total points, GW rank, overall rank, GW transfers etc. for each GW        
    '''
    # Loading classic league information from FPL API  
    league_manager_json = requests.get(f'https://fantasy.premierleague.com/api/leagues-classic/{league_id}/standings/').json()
    # Normalizing JSON to convert data to tabular form    
    league_manager_df = pd.json_normalize(league_manager_json,['standings','results'])
    # Renaming columns
    league_manager_df.rename(columns={'entry': 'team_id', 'entry_name': 'team_name', 'rank':'league_rank'}, inplace=True)
    # Creating final dataframe sorted by rank
    league_manager_df = league_manager_df[['team_id','team_name','league_rank']].sort_values('league_rank').reset_index(drop = True)
    
    # Creating empty dataframe to store data for each manager generated by loop 
    gw_perf_df=pd.DataFrame()
    # Iterating through every team_id in league_manager_df
    for i in league_manager_df.loc[:,'team_id']:
        # Obtaining GW history for each manager in the mini league
        gw_data_json = requests.get(f'https://fantasy.premierleague.com/api/entry/{i}/history/').json()
        # Normalizing JSON to convert data to tabular form
        raw_df = pd.json_normalize(gw_data_json,['current'])
        # Adding column to calculate net GW points
        raw_df['net_event_points'] = raw_df['points'] - raw_df['event_transfers_cost']
        # Appending manager's team_id
        raw_df['team_id'] = i
        # Appending data for each manager in the dataframe created above  
        gw_perf_df = gw_perf_df.append(raw_df,ignore_index=True)
    
    # Merging league_manager_df and gw_perf_df to obtain final dataframe 
    manager_gw_perf_df = pd.merge(league_manager_df, gw_perf_df, how= 'inner', on= 'team_id', left_index=False, right_index=False)
    return(manager_gw_perf_df)

def chart_race_data(league_id):
    '''
    Function to create a pivoted dataframe having team_name as columns and the total points after each GW as rows.
    This dataframe serves as input to create the bar chart race.
    
        Parameters:
            league_id: Id of the classic league, can be obtained from the URL of the classic league
            
        Returns:
            chart_race_df: Dataframe containing data GW level total points for each manager in the classic league which 
            serves as input for creating the bar chart race.        
    '''    
    # Pulling GW level performance data by calling the classic_league_gw_data() function 
    manager_gw_perf_df = classic_league_gw_data(league_id)
    
    # Pivoting manager_gw_perf_df to transform data in required format
    chart_race_df = manager_gw_perf_df[['team_name','event','total_points']].pivot_table(index=['event'], columns='team_name', values='total_points')
    return(chart_race_df)

### League Id and Top 'n' Input
1. League Id can be obtained from the URL of the classic league
2. Note that in case mini league has >50 managers, the FPL API returns data only for top 50 managers by rank
3. Top 'n' determines the total number of managers for which the chart will be created

In [3]:
# User input needed
league_id = 9418 # League id of Official /r/FantasyPL Classic League taken as an example
top_n = 10 # Enter a number between 1 to 50

### Exploring GW Performance Data of a Manager
Even though data in this table is not used to create the bar chart race, it can be used to perform analysis of perfomance of different managers in the mini league

In [4]:
# Calling classic_league_gw_data function to fetch GW level data
perf_df = classic_league_gw_data(league_id)
perf_df.head(38)

team_id     team_name  league_rank  event  points  total_points     rank  \
0    420518  Andromeda FC            1      1      71            71   773592   
1    420518  Andromeda FC            1      2      55           122  3705816   
2    420518  Andromeda FC            1      3      46           168  2660745   
3    420518  Andromeda FC            1      4      64           232  1333290   
4    420518  Andromeda FC            1      5      80           312   799516   
5    420518  Andromeda FC            1      6      40           352  5247632   
6    420518  Andromeda FC            1      7      71           423   608713   
7    420518  Andromeda FC            1      8      71           494   896193   
8    420518  Andromeda FC            1      9      77           571   478462   
9    420518  Andromeda FC            1     10      62           633   592406   
10   420518  Andromeda FC            1     11      72           705  1989232   
11   420518  Andromeda FC            1     12      55           756  3237500   
12   420518  Andromeda FC            1     13      62           818   201994   
13   420518  Andromeda FC            1     14      91           909   212323   
14   420518  Andromeda FC            1     15      56           965   987910   
15   420518  Andromeda FC            1     16      46          1011  1929884   
16   420518  Andromeda FC            1     17      69          1080  1572284   
17   420518  Andromeda FC            1     18      51          1127   813218   
18   420518  Andromeda FC            1     19     133          1256    57317   
19   420518  Andromeda FC            1     20      43          1299  3503288   
20   420518  Andromeda FC            1     21      79          1378   281092   
21   420518  Andromeda FC            1     22     101          1479    61335   
22   420518  Andromeda FC            1     23      81          1560   511452   
23   420518  Andromeda FC            1     24      86          1646  1351795   
24   420518  Andromeda FC            1     25      87          1733   267996   
25   420518  Andromeda FC            1     26     117          1846    89831   
26   420518  Andromeda FC            1     27      68          1910  2819503   
27   420518  Andromeda FC            1     28      48          1958  2734874   
28   420518  Andromeda FC            1     29      50          2008   875248   
29   420518  Andromeda FC            1     30      63          2071   875242   
30   420518  Andromeda FC            1     31      77          2148    55409   
31   420518  Andromeda FC            1     32      71          2219   524623   
32   420518  Andromeda FC            1     33      73          2292    28214   
33   420518  Andromeda FC            1     34      42          2334  3366362   
34   420518  Andromeda FC            1     35     124          2458   375293   
35   420518  Andromeda FC            1     36      67          2525   140488   
36   420518  Andromeda FC            1     37      46          2571  3663355   
37   420518  Andromeda FC            1     38      58          2629  2046028   

    rank_sort  overall_rank  bank  value  event_transfers  \
0      781241        773592    10   1000                0   
1     3707113       1649763     0   1002                2   
2     2664786       1494062     5   1005                1   
3     1336021        956160    15   1011                1   
4      802182        509427     0   1014                0   
5     5252137        819785     0   1023                0   
6      610541        436992     6   1027                1   
7      899993        308290     9   1032                1   
8      480591        153284    23   1036                1   
9      594516         90231    15   1038                2   
10    1993505         88613     4   1040                1   
11    3241221        143646     1   1041                2   
12     203146         70248     0   1043                1   
13     214102         31243  

### Taking a Peek at Data Used to Create Bar Chart Race

In [5]:
# Calling chart_race_data function to fetch the final df
df = chart_race_data(league_id)
df

team_name  A.S. Avalon  Allison Wonderland  Andromeda FC  Atletico Madras  \
event                                                                       
1                   76                  84            71               66   
2                  153                 157           122              130   
3                  208                 201           168              166   
4                  272                 248           232              235   
5                  358                 332           312              322   
6                  391                 375           352              370   
7                  455                 439           423              426   
8                  519                 512           494              499   
9                  580                 584           571              539   
10                 647                 644           633              593   
11                 727                 731           705              662   
12                 785                 787           756              734   
13                 842                 852           818              777   
14                 937                 948           909              870   
15                 993                1007           965              932   
16                1051                1068          1011             1000   
17                1111                1140          1080             1065   
18                1160                1182          1127             1124   
19                1306                1284          1256             1244   
20                1358                1346          1299             1289   
21                1414                1397          1378             1354   
22                1483                1470          1479             1425   
23                1551                1539          1560             1516   
24                1640                1653          1646             1604   
25                1733                1730          1733             1685   
26                1818                1821          1846             1795   
27                1885                1883          1910             1866   
28                1934                1944          1958             1923   
29                1986                1990          2008             1962   
30                2051                2049          2071             2029   
31                2105                2098          2148             2096   
32                2180                2179          2219             2175   
33                2239                2232          2292             2263   
34                2262                2269          2334             2299   
35                2392                2397          2458             2421   
36                2443                2455          2525             2479   
37                2498                2512          2571             2518   
38                2560                2582          2629             2585   

team_name  BIAWAK CIRIT  BSC Yang Boys  Babfasio  Carcavelhos  Catujalense FC  \
event                                                                           
1                    64             94        78           83              74   
2                   112            167       168          162             141   
3                   141            206       215          196             193   
4                   221            282       298          269             265   
5                   305            372       373          364             336   
6                   362            420       416          414             390   
7                   424            475       465          473             440   
8                   505            551       542          551             528   
9                   573            607       604          621             587   
10                  632     

### Creating the Bar Chart Race

The chart can be saved by clicking on the three dots on the bottom right of the visualization and selecting download

In [6]:
# Obtaining league name 

league_json = requests.get(f'https://fantasy.premierleague.com/api/leagues-classic/{league_id}/standings/').json()
league_name = league_json['league']['name']

# Determining number of bars in chart, in case total managers in league are < top_n

if len(df.columns)>=top_n:
    nbar = top_n
else:
    nbar = len(chart_race_df.columns)

# Plotting race bar chart

bcr.bar_chart_race(df
                   ,n_bars=nbar
                   ,steps_per_period=30
                   ,period_length=1250
                   ,interpolate_period=False
                   ,filter_column_colors = True
                   ,period_label={'x': .99, 'y': .1, 'ha': 'right', 'va': 'baseline'}
                   ,period_fmt='GW:{x:,.0f}'
                   ,dpi=144
                   ,title=f'{league_name} Top {top_n} League Position')